# Compare Models

Create object to automated model comparisons

In [1]:
import arithmetic_datasets as ad

from tensorflow.keras.layers import Input, Lambda, Dense, concatenate
from tensorflow.keras.models import Model

import matplotlib.pyplot as plt
import random
import numpy as np

from tensorflow.keras.callbacks import EarlyStopping

import numpy as np
import tensorflow as tf
import random
import keras
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.metrics import Metric

Using TensorFlow backend.


### ModelComparator

```
mc = ModelComparator()
mc.add_model(name, model)
mc.add_training_set(name, data)

mc.train_models(epochs, batches, **kwargs)

mc.compare_min(metric)
mc.compare_max(metric)

mc.history_for(model_name, training_set_name)
```

In [8]:
class ModelComparator:
    def __init__(self):
        self.models = {}
        self.training_sets = {}
        self.testing_sets = {}
        self.histories = {}
    
    def add_model(self, name, model):
        self.models[name] = model
    
    def add_training_set(self, name, data):
        self.training_sets[name] = data
        
    def add_testing_set(self, name, data):
        self.testing_sets[name] = data
        
    def train_models(self, **kwargs):
        for model_name in self.models:
            for tset_name in self.training_sets:
                print(f"MODEL {model_name} TRAINING ON DATASET {tset_name}")
                
                model = self.models[model_name]()
                
                history = model.fit(
                    self.training_sets[tset_name][0], self.training_sets[tset_name][1],
                    **kwargs
                )
                
                self.histories[(model_name, tset_name)] = history
    
    def compare_min(self, metric):
        result = {}
        minimum = None
        min_name = None
        for hkey in self.histories:
            history = self.histories[hkey].history
            result[hkey] = np.amin(history[metric])
            if minimum == None or minimum >= result[hkey]:
                minimum = result[hkey]
                min_name = hkey
        return result, {"name" : min_name, "value":minimum}
            
    
    def compare_max(self, metric):
        result = {}
        maximum = None
        max_name = None
        for hkey in self.histories:
            history = self.histories[hkey].history
            result[hkey] = np.amax(history[metric])
            if maximum == None or maximum >= result[hkey]:
                maximum = result[hkey]
                max_name = hkey
        return result, {"name" : max_name, "value": maximum}
    
    def history_for(self, model_name, training_set_name):
        return self.histories[(model_name, training_set_name)]
    
    def test_models(self, use_training_sets=False, acc_range=0.5):
        if use_training_sets:
            testing_sets = self.training_sets
        else:
            testing_sets = self.testing_sets
        
        for model_name in self.models:
            for tset_name in testing_sets:
                print(f"MODEL {model_name} TESTING ON DATASET {tset_name}")
                model = self.models[model_name]()
                
                x_test = testing_sets[tset_name][0]
                y_test = testing_sets[tset_name][1]
                
                pred = model.predict(x_test)
                
                test_total = 0
                acc_count = 0
                for a in range(len(x_test)):
                    x = x_test[a]
                    y = y_test[a]
                    yp = pred[a][0]
                    print(f"\tinput={x[0]} expected_output={[y]} prediction={yp} \n\t\tdifference={yp - y} \n\t\t%-different from actual={abs(yp - y)/y}")

                    if abs(yp - y) <= acc_range:
                        acc_count = acc_count + 1

                    test_total = test_total + 1

                    print(f"\t\t accuracy={acc_count / test_total}")

### Create Models

### Create Models

In [9]:
def nondense_model():
    # Input layer of 3 neurons 
    inp = Input(shape=(1,3))
    
    #128 layer
    d2_out = Dense(128)(inp)

    #grab first, 2nd half of the 128 layer
    d2_out_p1 = Lambda(lambda x: x[:,:,0:64])(d2_out)
    d2_out_p2 = Lambda(lambda x: x[:,:,64:128])(d2_out)

    #64 layer(s)
    d3_out = Dense(64)(d2_out_p1)
    d4_out = Dense(64)(d2_out_p2)

    #grab output nodes from both 64 layers
    d5_out = concatenate([d3_out, d4_out])
    
    o = Dense(1)(d5_out)
    
    model = Model(inp, o)

    model.compile(
        loss="MeanSquaredError",
        metrics=['accuracy']
    )
    
    return model

def dense_model_5L():
    model_5layer = tf.keras.models.Sequential([
        tf.keras.layers.Dense(1024, input_shape=(1,3)),
        tf.keras.layers.Dense(512),
        tf.keras.layers.Dense(256),
        tf.keras.layers.Dense(128),
        tf.keras.layers.Dense(64),
        tf.keras.layers.Dense(1)
    ])
    
    model_5layer.compile(
        loss="MeanSquaredError",
        metrics=['accuracy'] #Acc not working, in testing
    )

    return model_5layer

### Datasets

In [10]:
num_examples = 20000
rstart = -50000
rend = 50000

add_setX, add_setY = ad.gen_data_add(num_examples, rstart, rend)
sub_setX, sub_setY = ad.gen_data_sub(num_examples, rstart, rend)

add_setX = add_setX.reshape(num_examples, 1, 3)
sub_setX = sub_setX.reshape(num_examples, 1, 3)

# 50-50
step = int(0.5*num_examples)

addsub_set1X = np.concatenate((add_setX[:step], sub_setX[step:]))
addsub_set1Y = np.concatenate((add_setY[:step], sub_setY[step:]))

# 80-20
step = int(0.8*num_examples)
addsub_set2X = np.concatenate((add_setX[:step], sub_setX[step:]))
addsub_set2Y = np.concatenate((add_setY[:step], sub_setY[step:]))

# MULT and DIV
mult_setX, mult_setY = ad.gen_data_mult(num_examples, rstart, rend)
div_setX, div_setY = ad.gen_data_div(num_examples, rstart, rend)

mult_setX = mult_setX.reshape(num_examples, 1, 3)
div_setX = div_setX.reshape(num_examples, 1, 3)

# MD 50-50
step = int(0.5*num_examples)
multdiv_set1X = np.concatenate((mult_setX[:step], div_setX[step:]))
multdiv_set1Y = np.concatenate((mult_setY[:step], div_setY[step:]))

# MD 80-20
step = int(0.8*num_examples)
multdiv_set2X = np.concatenate((mult_setX[:step], div_setX[step:]))
multdiv_set2Y = np.concatenate((mult_setY[:step], div_setY[step:]))

### Build ModelComparator

In [11]:
mc = ModelComparator()

mc.add_model("nondense_model", nondense_model)
#mc.add_model("dense_model", dense_model_5L)

mc.add_training_set("addition", (add_setX, add_setY))
mc.add_training_set("subtraction", (sub_setX, sub_setY))
# mc.add_training_set("add-sub 50/50", (addsub_set1X, addsub_set1Y))
# mc.add_training_set("add-sub 80/20", (addsub_set2X, addsub_set2Y))
# mc.add_training_set("multiplication", (mult_setX, mult_setY))
# mc.add_training_set("division", (div_setX, div_setY))
# mc.add_training_set("mult-div 50/50", (multdiv_set1X, multdiv_set1Y))
# mc.add_training_set("mult-div 80/20", (multdiv_set2X, multdiv_set2Y))



### Train Models

In [12]:
num_epochs = 100
batch_size = num_examples

mc.train_models(
    batch_size=batch_size,
    epochs=num_epochs
)

MODEL nondense_model TRAINING ON DATASET addition
Epoch 1/100
1/1 [==============================] - 0s 2ms/step - loss: 825697152.0000 - accuracy: 0.0000e+00
Epoch 2/100
1/1 [==============================] - 0s 997us/step - loss: 292059968.0000 - accuracy: 0.0000e+00
Epoch 3/100
1/1 [==============================] - 0s 2ms/step - loss: 113127904.0000 - accuracy: 0.0000e+00
Epoch 4/100
1/1 [==============================] - 0s 2ms/step - loss: 41376448.0000 - accuracy: 0.0000e+00
Epoch 5/100
1/1 [==============================] - 0s 995us/step - loss: 13675169.0000 - accuracy: 0.0000e+00
Epoch 6/100
1/1 [==============================] - 0s 2ms/step - loss: 4006542.5000 - accuracy: 0.0000e+00
Epoch 7/100
1/1 [==============================] - 0s 2ms/step - loss: 1031974.3125 - accuracy: 0.0000e+00
Epoch 8/100
1/1 [==============================] - 0s 983us/step - loss: 232936.4531 - accuracy: 0.0000e+00
Epoch 9/100
1/1 [==============================] - 0s 2ms/step - loss: 46349.4531

1/1 [==============================] - 0s 2ms/step - loss: 11254163.0000 - accuracy: 0.0000e+00
Epoch 77/100
1/1 [==============================] - 0s 2ms/step - loss: 14175371.0000 - accuracy: 0.0000e+00
Epoch 78/100
1/1 [==============================] - 0s 999us/step - loss: 8116275.0000 - accuracy: 0.0000e+00
Epoch 79/100
1/1 [==============================] - 0s 2ms/step - loss: 4108060.7500 - accuracy: 0.0000e+00
Epoch 80/100
1/1 [==============================] - 0s 2ms/step - loss: 1888177.3750 - accuracy: 0.0000e+00
Epoch 81/100
1/1 [==============================] - 0s 2ms/step - loss: 1082644.6250 - accuracy: 0.0000e+00
Epoch 82/100
1/1 [==============================] - 0s 2ms/step - loss: 711034.1875 - accuracy: 0.0000e+00
Epoch 83/100
1/1 [==============================] - 0s 2ms/step - loss: 589248.1250 - accuracy: 0.0000e+00
Epoch 84/100
1/1 [==============================] - 0s 2ms/step - loss: 576731.2500 - accuracy: 0.0000e+00
Epoch 85/100
1/1 [======================

1/1 [==============================] - 0s 999us/step - loss: 2959553.7500 - accuracy: 0.0000e+00
Epoch 52/100
1/1 [==============================] - 0s 997us/step - loss: 2269500.5000 - accuracy: 0.0000e+00
Epoch 53/100
1/1 [==============================] - 0s 2ms/step - loss: 1930725.0000 - accuracy: 0.0000e+00
Epoch 54/100
1/1 [==============================] - 0s 3ms/step - loss: 1820117.7500 - accuracy: 0.0000e+00
Epoch 55/100
1/1 [==============================] - 0s 999us/step - loss: 1965447.1250 - accuracy: 0.0000e+00
Epoch 56/100
1/1 [==============================] - 0s 2ms/step - loss: 2366058.5000 - accuracy: 0.0000e+00
Epoch 57/100
1/1 [==============================] - 0s 996us/step - loss: 3273815.2500 - accuracy: 0.0000e+00
Epoch 58/100
1/1 [==============================] - 0s 2ms/step - loss: 4759314.5000 - accuracy: 0.0000e+00
Epoch 59/100
1/1 [==============================] - 0s 3ms/step - loss: 7010805.5000 - accuracy: 0.0000e+00
Epoch 60/100
1/1 [===============

In [13]:
mc.test_models(use_training_sets=True)

MODEL nondense_model TESTING ON DATASET addition
	input=[-42451  25455     43] expected_output=[-16996] prediction=[-8471.932] 
		difference=[8524.068] %-different from actual=[-0.5015338]
		 accuracy=0.0
	input=[ 6149 39295    43] expected_output=[45444] prediction=[657.44995] 
		difference=[-44786.55] %-different from actual=[0.98553276]
		 accuracy=0.0
	input=[-25404 -21961     43] expected_output=[-47365] prediction=[-4591.9956] 
		difference=[42773.00439453] %-different from actual=[-0.90305087]
		 accuracy=0.0
	input=[ 2053 32676    43] expected_output=[34729] prediction=[-41.27954] 
		difference=[-34770.28] %-different from actual=[1.0011886]
		 accuracy=0.0
	input=[-35592  10115     43] expected_output=[-25477] prediction=[-6959.2734] 
		difference=[18517.727] %-different from actual=[-0.7268409]
		 accuracy=0.0
	input=[-21293 -40091     43] expected_output=[-61384] prediction=[-3569.514] 
		difference=[57814.48608398] %-different from actual=[-0.94184944]
		 accuracy=0.0
	inpu

	input=[-19310 -18852     43] expected_output=[-38162] prediction=[-3465.0625] 
		difference=[34696.9375] %-different from actual=[-0.90920123]
		 accuracy=0.0
	input=[ 7202 35193    43] expected_output=[42395] prediction=[912.3262] 
		difference=[-41482.67] %-different from actual=[0.9784803]
		 accuracy=0.0
	input=[-9065 46981    43] expected_output=[37916] prediction=[-2356.2793] 
		difference=[-40272.28] %-different from actual=[1.0621448]
		 accuracy=0.0
	input=[-44874  44271     43] expected_output=[-603] prediction=[-9179.988] 
		difference=[-8576.988] %-different from actual=[-14.223861]
		 accuracy=0.0
	input=[ 43095 -19731     43] expected_output=[23364] prediction=[8499.357] 
		difference=[-14864.643] %-different from actual=[0.6362199]
		 accuracy=0.0
	input=[46314 18271    43] expected_output=[64585] prediction=[8623.217] 
		difference=[-55961.78] %-different from actual=[0.8664826]
		 accuracy=0.0
	input=[ 10045 -17870     43] expected_output=[-7825] prediction=[2144.85] 

		difference=[-40955.473] %-different from actual=[0.95356166]
		 accuracy=0.0
	input=[ 2865 25691    43] expected_output=[28556] prediction=[204.81348] 
		difference=[-28351.188] %-different from actual=[0.9928277]
		 accuracy=0.0
	input=[-46746 -27846     43] expected_output=[-74592] prediction=[-8603.53] 
		difference=[65988.46972656] %-different from actual=[-0.88465881]
		 accuracy=0.0
	input=[ 7450 -2530    43] expected_output=[4920] prediction=[1448.916] 
		difference=[-3471.084] %-different from actual=[0.7055049]
		 accuracy=0.0
	input=[ 41670 -10497     43] expected_output=[31173] prediction=[8106.6943] 
		difference=[-23066.305] %-different from actual=[0.739945]
		 accuracy=0.0
	input=[-35675  -4663     43] expected_output=[-40338] prediction=[-6783.5723] 
		difference=[33554.42773438] %-different from actual=[-0.83183172]
		 accuracy=0.0
	input=[40230 33215    43] expected_output=[73445] prediction=[7264.1387] 
		difference=[-66180.86132812] %-different from actual=[0.9010

		difference=[-21422.688] %-different from actual=[0.6996763]
		 accuracy=0.0
	input=[-48320   8276     43] expected_output=[-40044] prediction=[-9373.349] 
		difference=[30670.65136719] %-different from actual=[-0.76592377]
		 accuracy=0.0
	input=[  1135 -15456     43] expected_output=[-14321] prediction=[406.93347] 
		difference=[14727.934] %-different from actual=[-1.0284152]
		 accuracy=0.0
	input=[43666 24693    43] expected_output=[68359] prediction=[8032.755] 
		difference=[-60326.24511719] %-different from actual=[0.88249163]
		 accuracy=0.0
	input=[42640 16648    43] expected_output=[59288] prediction=[7940.543] 
		difference=[-51347.457] %-different from actual=[0.8660683]
		 accuracy=0.0
	input=[ 17684 -13808     43] expected_output=[3876] prediction=[3555.3555] 
		difference=[-320.64453] %-different from actual=[0.08272563]
		 accuracy=0.0
	input=[-46051 -27322     43] expected_output=[-73373] prediction=[-8477.203] 
		difference=[64895.796875] %-different from actual=[-0.8

		difference=[-6908.412] %-different from actual=[-3.3601227]
		 accuracy=0.0
	input=[ 13099 -30950     43] expected_output=[-17851] prediction=[2899.398] 
		difference=[20750.398] %-different from actual=[-1.1624222]
		 accuracy=0.0
	input=[ 30324 -41398     43] expected_output=[-11074] prediction=[6334.1255] 
		difference=[17408.125] %-different from actual=[-1.5719817]
		 accuracy=0.0
	input=[  8856 -13113     43] expected_output=[-4257] prediction=[1855.4319] 
		difference=[6112.4316] %-different from actual=[-1.4358543]
		 accuracy=0.0
	input=[-48025 -21553     43] expected_output=[-69578] prediction=[-8930.102] 
		difference=[60647.8984375] %-different from actual=[-0.87165337]
		 accuracy=0.0
	input=[ -7842 -12944     43] expected_output=[-20786] prediction=[-1345.0857] 
		difference=[19440.914] %-different from actual=[-0.93528885]
		 accuracy=0.0
	input=[-33896  -2798     43] expected_output=[-36694] prediction=[-6467.0015] 
		difference=[30226.99853516] %-different from actua

...

		difference=[-41473.6] %-different from actual=[0.85597295]
		 accuracy=0.0
	input=[ 8278 13397   145] expected_output=[-5119] prediction=[-1757.6624] 
		difference=[3361.3376] %-different from actual=[-0.6566395]
		 accuracy=0.0
	input=[-45189  12541    145] expected_output=[-57730] prediction=[-6477.8657] 
		difference=[51252.13427734] %-different from actual=[-0.8877903]
		 accuracy=0.0
	input=[-28581  -9340    145] expected_output=[-19241] prediction=[-872.12775] 
		difference=[18368.873] %-different from actual=[-0.9546735]
		 accuracy=0.0
	input=[-34263  28074    145] expected_output=[-62337] prediction=[-8383.916] 
		difference=[53953.08398438] %-different from actual=[-0.86550658]
		 accuracy=0.0
	input=[30411 31208   145] expected_output=[-797] prediction=[-3066.5806] 
		difference=[-2269.5806] %-different from actual=[-2.8476543]
		 accuracy=0.0
	input=[-42491 -44529    145] expected_output=[2038] prediction=[4435.516] 
		difference=[2397.516] %-different from actual=[1.1764

		difference=[30421.14331055] %-different from actual=[-0.91234235]
		 accuracy=0.0
	input=[27600 31217   145] expected_output=[-3617] prediction=[-3324.836] 
		difference=[292.16406] %-different from actual=[-0.08077525]
		 accuracy=0.0
	input=[ 16777 -25889    145] expected_output=[42666] prediction=[6361.1475] 
		difference=[-36304.85] %-different from actual=[0.8509083]
		 accuracy=0.0
	input=[-28502  38748    145] expected_output=[-67250] prediction=[-9853.1875] 
		difference=[57396.8125] %-different from actual=[-0.8534842]
		 accuracy=0.0
	input=[-17993    888    145] expected_output=[-18881] prediction=[-1817.4534] 
		difference=[17063.547] %-different from actual=[-0.9037417]
		 accuracy=0.0
	input=[-36691 -21495    145] expected_output=[-15196] prediction=[659.56085] 
		difference=[15855.561] %-different from actual=[-1.0434035]
		 accuracy=0.0
	input=[  5843 -26172    145] expected_output=[32015] prediction=[5416.041] 
		difference=[-26598.959] %-different from actual=[0.830

		difference=[-77080.859375] %-different from actual=[0.85596894]
		 accuracy=0.0
	input=[  -668 -47031    145] expected_output=[46363] prediction=[8720.57] 
		difference=[-37642.43] %-different from actual=[0.8119067]
		 accuracy=0.0
	input=[-32861 -21684    145] expected_output=[-11177] prediction=[1044.4697] 
		difference=[12221.47] %-different from actual=[-1.0934482]
		 accuracy=0.0
	input=[21160 18384   145] expected_output=[2776] prediction=[-1513.9941] 
		difference=[-4289.994] %-different from actual=[1.5453869]
		 accuracy=0.0
	input=[-18411  15135    145] expected_output=[-33546] prediction=[-4518.556] 
		difference=[29027.44384766] %-different from actual=[-0.86530268]
		 accuracy=0.0
	input=[17236 -5710   145] expected_output=[22946] prediction=[2631.3235] 
		difference=[-20314.676] %-different from actual=[0.8853254]
		 accuracy=0.0
	input=[-6451 33658   145] expected_output=[-40109] prediction=[-6889.095] 
		difference=[33219.90478516] %-different from actual=[-0.8282406

		difference=[60566.703125] %-different from actual=[-0.88007415]
		 accuracy=0.0
	input=[-38754 -42532    145] expected_output=[3778] prediction=[4403.3457] 
		difference=[625.3457] %-different from actual=[0.16552295]
		 accuracy=0.0
	input=[ -7676 -24072    145] expected_output=[16396] prediction=[3789.579] 
		difference=[-12606.421] %-different from actual=[0.7688717]
		 accuracy=0.0
	input=[-22014 -18770    145] expected_output=[-3244] prediction=[1489.8651] 
		difference=[4733.865] %-different from actual=[-1.459268]
		 accuracy=0.0
	input=[31709 35940   145] expected_output=[-4231] prediction=[-3832.5762] 
		difference=[398.42383] %-different from actual=[-0.09416777]
		 accuracy=0.0
	input=[32243 11202   145] expected_output=[21041] prediction=[840.01636] 
		difference=[-20200.984] %-different from actual=[0.9600772]
		 accuracy=0.0
	input=[-28757   9960    145] expected_output=[-38717] prediction=[-4495.615] 
		difference=[34221.38476562] %-different from actual=[-0.88388524]


		difference=[3765.108] %-different from actual=[-0.9033368]
		 accuracy=0.0
	input=[37162 12636   145] expected_output=[24526] prediction=[1020.966] 
		difference=[-23505.033] %-different from actual=[0.95837206]
		 accuracy=0.0
	input=[ 3878 13793   145] expected_output=[-9915] prediction=[-2233.291] 
		difference=[7681.709] %-different from actual=[-0.7747563]
		 accuracy=0.0
	input=[-21588  -9441    145] expected_output=[-12147] prediction=[-214.96332] 
		difference=[11932.037] %-different from actual=[-0.9823032]
		 accuracy=0.0
	input=[-17035 -39501    145] expected_output=[22466] prediction=[5819.218] 
		difference=[-16646.781] %-different from actual=[0.74097663]
		 accuracy=0.0
	input=[-25199  25874    145] expected_output=[-51073] prediction=[-7145.39] 
		difference=[43927.60986328] %-different from actual=[-0.86009457]
		 accuracy=0.0
	input=[ 29596 -21087    145] expected_output=[50683] prediction=[6633.6436] 
		difference=[-44049.355] %-different from actual=[0.869115]
		 

### compare min loss

In [ ]:
models_min_loss, min_loss = mc.compare_min("loss")

In [ ]:
models_min_loss